In [36]:
import simpy
import numpy as np
import os
import xlsxwriter
import pandas as pd

## Variables:

# 
simulationTime = 10000
seedValue = 0
##
cwd = os.getcwd() ## obtain current directory path

## to collect arrival times and server times
serv1_time    = []
serv2_time    = []

##
trace = []
listArrived   = []
listServed    = []
listServed1   = []

##
obs_times  = []
masterObsArray = []

##-- Defining of service time functions

## 1.0: arrival function at server 1
def generate_interarrival():
    return np.random.exponential(1.0)

##2.0 service time for server 1
def generate_service_1():
    return np.random.exponential(0.7)


##3.0 service time for server 2
def generate_service_2():
    return np.random.exponential(0.9)

##4.0 operation to add an index number/token to a given customer
def service_run(env, server1, server2):
    i=0
    while True:
        i += 1
        yield env.timeout(generate_interarrival())        
        env.process(customer(env, i, server1, server2))

##5.0 function defining operation environment
def customer(env, customer, server1, server2):
    with server1.request() as request:
            temp = []
            t_arrival_serv1 = env.now
            
            ## recording arrival time at server 1 for each customer
             
            temp.append(int(customer))                    # Customer index number
            temp.append(float(t_arrival_serv1))           # Arrival time at server 1
            ##arrival_time1.append(temp)
            
            print(env.now,"\t","Customer {} arrives for service at server 1 ".format(customer))
            trace.append(str(env.now)+":  "+"Customer {} arrives for service at server 1 ".format(customer))
            listArrived.append(int("{}".format(customer)))
            yield request
            
            t_start_serv1 = env.now           
            print (env.now,"\t","Customer {} is being served at server 1".format(customer))
            trace.append(str(env.now)+":  "+"Customer {} is being served at server 1".format(customer))
            
            yield env.timeout(generate_service_1())
            print (env.now,"\t","Customer {} departs server 1".format(customer))
            trace.append(str(env.now)+":  "+"Customer {} departs server 1".format(customer))
            listServed1.append(int("{}".format(customer)))
            t_depart_server1 = env.now
            
            ##temp = []
            temp.append(int(customer))                       # Customer index number
            temp.append(t_start_serv1)                       # Service start time at server 1
            temp.append(t_depart_server1 - t_start_serv1)    # Service time at server 1
            ##serv1_time.append(temp)
            
            ##temp = []
            temp.append(int(customer))                       # Customer index number
            temp.append(t_start_serv1 - t_arrival_serv1)     # Wait time at server 1
            temp.append(t_depart_server1 - t_arrival_serv1)  # Response time at server 1
            temp.append(t_depart_server1)                    # Departure time at server 1
            serv1_time.append(temp)
              
    with server2.request() as request:
            temp = [] 
            t_arrival_serv2 = env.now
            
            ## recording arrival time at server 1 for each customer
            
            temp.append(int(customer))                       # Customer index number
            temp.append(float(t_arrival_serv2))              # Arrival time at server 2
            ##arrival_time2.append(temp) 
            
            print (env.now,"\t","Customer {} arrives for service at server 2".format(customer))
            trace.append(str(env.now)+":  "+"Customer {} arrives for service at server 2".format(customer))            
            yield request
            
            t_start_serv2 = env.now
            print (env.now,"\t","Customer {} is being served at server 2".format(customer))
            trace.append(str(env.now)+":  "+"Customer {} is being served at server 2".format(customer))
            
            yield env.timeout(generate_service_2())
            print (env.now,"\t","Customer {} departs server 2".format(customer))
            trace.append(str(env.now)+":  "+"Customer {} departs server 2".format(customer))
            listServed.append(int("{}".format(customer)))
            t_depart_server2 = env.now
            
            ##temp = []
            temp.append(int(customer))                         # Customer index number
            temp.append(t_start_serv2)                         # Service start time at server 2
            temp.append(t_depart_server2 - t_start_serv2)      # Service time at server 2
            #serv2_time.append(temp)
            
            #temp = []
            temp.append(int(customer))                         # Customer index number
            temp.append(t_start_serv2 - t_arrival_serv2)       # Wait time at server 2
            temp.append(t_depart_server2 - t_arrival_serv2)    # Response time at server 2
            temp.append(t_depart_server2)                      # Departure time at server 2
            serv2_time.append(temp)

##6.0 function meant for keeping track of observartions
def observe(env, server1, server2):
    while True:
        ## Dummy array to append time and string length values
        temp = [] 
        
        obs_times.append(env.now)
        
        ## appending values into a dummy array
        temp.append(env.now)
        temp.append(len(server1.queue))
        temp.append(len(server2.queue))
        
        ## append temp into masterObsArray
        masterObsArray.append(temp)
        ## We are timing out the yield by 1.0 minute before making 
        ## succesive observations
        yield env.timeout(1)        

np.random.seed(seedValue)
env = simpy.Environment()

server1 = simpy.Resource(env, capacity=1)
server2 = simpy.Resource(env, capacity=1)
env.process(service_run(env, server1, server2))
env.process(observe(env, server1, server2))
env.run(until = simulationTime)        
        

servDF1 = pd.DataFrame(serv1_time, columns = ['CustomerIndex1', 'ArrivalTime','CustomerIndex2', 'ServiceStart', 'ServiceTime', 'CustomerIndex3', 'WaitTime', 'ResponseTime', 'DepartureTime'])
servDF2 = pd.DataFrame(serv2_time, columns = ['CustomerIndex1', 'ArrivalTime','CustomerIndex2', 'ServiceStart', 'ServiceTime', 'CustomerIndex3', 'WaitTime', 'ResponseTime', 'DepartureTime'])
df  = pd.DataFrame(masterObsArray, columns = ['Time', 'Q1Length', 'Q2Length']) 

## Operation on server 1
    # Creating a column to record previous customers departure time or when a system was freed
servDF1['PreviousDepartureTime'] = servDF1.DepartureTime.shift(1)

    # Creating a column to calculate idle time for a given system by calculating difference between Current customer
    # arrival time and previous customers departure time
servDF1['IdleTime'] = servDF1.ArrivalTime - servDF1.PreviousDepartureTime

    # Creating a column to calculate how long a system was idle by eliminating negative values
mask = servDF1.IdleTime < 0
column_name = 'IdleTime'
servDF1.loc[mask, column_name] = 0


## Operation on server 1
    # Creating a column to record previous customers departure time or when a system was freed
servDF2['PreviousDepartureTime'] = servDF2.DepartureTime.shift(1)

    # Creating a column to calculate idle time for a given system by calculating difference between Current customer
    # arrival time and previous customers departure time
servDF2['IdleTime'] = servDF2.ArrivalTime - servDF2.PreviousDepartureTime

    # Creating a column to calculate how long a system was idle by eliminating negative values
mask = servDF2.IdleTime < 0
column_name = 'IdleTime'
servDF2.loc[mask, column_name] = 0

## Write output to an Excel file
#------------------------------------------------------------------------------#
# Create an new Excel file and add a worksheet.
workbook = xlsxwriter.Workbook(cwd+'//'+'TraceOutput.xlsx')

##Write Outputs to output tab
worksheet = workbook.add_worksheet('Output')
worksheet.set_column('A:A', 100)
worksheet.write('A1', 'Description')
worksheet.write('A2', 'Maximum Length of Queue 1 waiting for Serv1')
worksheet.write('A3', 'Maximum Length of Queue 2 waiting for Serv2')
worksheet.write('A5', 'Maximum Wait Time of Q1')
worksheet.write('A6', 'Average Wait Time of Q1')
worksheet.write('A8', 'Maximum Wait Time of Q2')
worksheet.write('A9', 'Average Wait Time of Q2')
worksheet.write('A11', 'Total number of customers served by Serv1')
worksheet.write('A12', 'Total number of customers served by system')
worksheet.write('A14', 'Average service time at Serv1')
worksheet.write('A15', 'Max service time at Serv1')
worksheet.write('A16', 'Min service time at Serv1')
worksheet.write('A18', 'Average service time at Serv2')
worksheet.write('A19', 'Max service time at Serv2')
worksheet.write('A20', 'Min service time at Serv2')
worksheet.write('A22', 'Idle service time at Serv1')
worksheet.write('A23', 'Idle rate st Serv1')
worksheet.write('A24', 'Utilization rate st Serv1')
worksheet.write('A26', 'Idle service time at Serv2')
worksheet.write('A27', 'Idle rate st Serv2')
worksheet.write('A28', 'Utilization rate st Serv2')

worksheet.write('A35', '** Time has been expressed in minutes')
worksheet.write('A36', '** Simulated for (minutes)')
worksheet.write('A37', '** Seed Value')

worksheet.write('B1', 'Value')
worksheet.write('B2', max(df['Q1Length']))
worksheet.write('B3', max(df['Q2Length']))
worksheet.write('B5', max(servDF1['WaitTime']))
worksheet.write('B6', servDF1['WaitTime'].mean())
worksheet.write('B8', max(servDF2['WaitTime']))
worksheet.write('B9', servDF2['WaitTime'].mean())
worksheet.write('B11', max(servDF1['CustomerIndex1']))
worksheet.write('B12', max(servDF2['CustomerIndex1']))
worksheet.write('B14', servDF1['ServiceTime'].mean())
worksheet.write('B15', max(servDF1['ServiceTime']))
worksheet.write('B16', min(servDF1['ServiceTime']))
worksheet.write('B18', servDF2['ServiceTime'].mean())
worksheet.write('B19', max(servDF2['ServiceTime']))
worksheet.write('B20', min(servDF2['ServiceTime']))
worksheet.write('B22', servDF1['IdleTime'].sum())
worksheet.write('B23', servDF1['IdleTime'].sum()/simulationTime)
worksheet.write('B24', 1 - (servDF1['IdleTime'].sum()/simulationTime))
worksheet.write('B26', servDF2['IdleTime'].sum())
worksheet.write('B27', servDF2['IdleTime'].sum()/simulationTime)
worksheet.write('B28', 1 - (servDF2['IdleTime'].sum()/simulationTime))
worksheet.write('B36', simulationTime)
worksheet.write('B37', seedValue)

# Widen the first column to make the text clearer.
worksheet = workbook.add_worksheet('Trace')
worksheet.set_column('A:A', 150)

## Write trace output to excel sheet Trace
cell = 0
for value in trace:   
    cell = cell+1
    cellValue = 'A'+str(cell)
    worksheet.write(cellValue, str(value))

workbook.close()

# Create a Pandas Excel writer using XlsxWriter as the engine.
writer = pd.ExcelWriter('LogFile.xlsx', engine='xlsxwriter')
df.to_excel(writer, sheet_name='Queue')
servDF1.to_excel(writer, sheet_name='ServS1')
servDF2.to_excel(writer, sheet_name='ServS2')
writer.save()
##write data frames to excel



0.79587450816311 	 Customer 1 arrives for service at server 1 
0.79587450816311 	 Customer 1 is being served at server 1
1.4421307102259582 	 Customer 1 departs server 1
1.4421307102259582 	 Customer 1 arrives for service at server 2
1.4421307102259582 	 Customer 1 is being served at server 2
2.0518052711289476 	 Customer 2 arrives for service at server 1 
2.0518052711289476 	 Customer 2 is being served at server 1
2.150611747311502 	 Customer 1 departs server 2
2.6028537622244468 	 Customer 3 arrives for service at server 1 
2.7785167775894744 	 Customer 2 departs server 1
2.7785167775894744 	 Customer 2 arrives for service at server 2
2.7785167775894744 	 Customer 2 is being served at server 2
2.7785167775894744 	 Customer 3 is being served at server 1
3.1783729613930864 	 Customer 4 arrives for service at server 1 
3.6619750622953395 	 Customer 5 arrives for service at server 1 
4.779688749318865 	 Customer 2 departs server 2
5.098955305027144 	 Customer 3 departs server 1
5.0989553

88.00904215977894 	 Customer 89 departs server 1
88.00904215977894 	 Customer 89 arrives for service at server 2
88.00904215977894 	 Customer 89 is being served at server 2
88.00904215977894 	 Customer 90 is being served at server 1
88.58036565547683 	 Customer 93 arrives for service at server 1 
88.9930955158675 	 Customer 94 arrives for service at server 1 
89.47313177698958 	 Customer 90 departs server 1
89.47313177698958 	 Customer 90 arrives for service at server 2
89.47313177698958 	 Customer 91 is being served at server 1
89.657635756849 	 Customer 91 departs server 1
89.657635756849 	 Customer 91 arrives for service at server 2
89.657635756849 	 Customer 92 is being served at server 1
91.42366374334578 	 Customer 89 departs server 2
91.42366374334578 	 Customer 90 is being served at server 2
91.74517623853163 	 Customer 92 departs server 1
91.74517623853163 	 Customer 92 arrives for service at server 2
91.74517623853163 	 Customer 93 is being served at server 1
92.2520164116574

170.09707307993116 	 Customer 168 departs server 2
170.09707307993116 	 Customer 169 is being served at server 2
170.10705421004502 	 Customer 170 departs server 1
170.10705421004502 	 Customer 170 arrives for service at server 2
170.10705421004502 	 Customer 171 is being served at server 1
170.56720340617292 	 Customer 176 arrives for service at server 1 
170.79652058386193 	 Customer 177 arrives for service at server 1 
170.97356382681906 	 Customer 169 departs server 2
170.97356382681906 	 Customer 170 is being served at server 2
170.97484287749595 	 Customer 171 departs server 1
170.97484287749595 	 Customer 171 arrives for service at server 2
170.97484287749595 	 Customer 172 is being served at server 1
171.21461224473273 	 Customer 178 arrives for service at server 1 
171.98854822774513 	 Customer 170 departs server 2
171.98854822774513 	 Customer 171 is being served at server 2
171.99916894101017 	 Customer 179 arrives for service at server 1 
172.0298707119378 	 Customer 180 ar

253.39059617908177 	 Customer 256 is being served at server 1
253.81998882195654 	 Customer 256 departs server 1
253.81998882195654 	 Customer 256 arrives for service at server 2
253.90674990005843 	 Customer 249 departs server 2
253.90674990005843 	 Customer 250 is being served at server 2
254.4359893344791 	 Customer 250 departs server 2
254.4359893344791 	 Customer 251 is being served at server 2
254.80465377580595 	 Customer 251 departs server 2
254.80465377580595 	 Customer 252 is being served at server 2
255.3480145723068 	 Customer 257 arrives for service at server 1 
255.3480145723068 	 Customer 257 is being served at server 1
256.7179913059473 	 Customer 252 departs server 2
256.7179913059473 	 Customer 253 is being served at server 2
257.1435054960696 	 Customer 253 departs server 2
257.1435054960696 	 Customer 254 is being served at server 2
258.24892363806975 	 Customer 258 arrives for service at server 1 
258.718303170869 	 Customer 257 departs server 1
258.718303170869 	 

347.8753025761181 	 Customer 340 arrives for service at server 1 
348.08467589391006 	 Customer 338 departs server 1
348.08467589391006 	 Customer 338 arrives for service at server 2
348.08467589391006 	 Customer 339 is being served at server 1
348.21434040424924 	 Customer 341 arrives for service at server 1 
348.235513040232 	 Customer 342 arrives for service at server 1 
348.5117461033635 	 Customer 339 departs server 1
348.5117461033635 	 Customer 339 arrives for service at server 2
348.5117461033635 	 Customer 340 is being served at server 1
348.76588769659537 	 Customer 343 arrives for service at server 1 
348.9823446353391 	 Customer 340 departs server 1
348.9823446353391 	 Customer 340 arrives for service at server 2
348.9823446353391 	 Customer 341 is being served at server 1
349.0451755992511 	 Customer 344 arrives for service at server 1 
349.6041435089907 	 Customer 341 departs server 1
349.6041435089907 	 Customer 341 arrives for service at server 2
349.6041435089907 	 Cus

...

9570.790471095592 	 Customer 9636 departs server 2
9570.790471095592 	 Customer 9637 is being served at server 2
9570.936452181593 	 Customer 9641 departs server 1
9570.936452181593 	 Customer 9641 arrives for service at server 2
9571.161688526536 	 Customer 9637 departs server 2
9571.161688526536 	 Customer 9638 is being served at server 2
9571.705364541122 	 Customer 9642 arrives for service at server 1 
9571.705364541122 	 Customer 9642 is being served at server 1
9571.934273142377 	 Customer 9643 arrives for service at server 1 
9572.175286528503 	 Customer 9644 arrives for service at server 1 
9572.293815541834 	 Customer 9642 departs server 1
9572.293815541834 	 Customer 9642 arrives for service at server 2
9572.293815541834 	 Customer 9643 is being served at server 1
9572.612453228981 	 Customer 9645 arrives for service at server 1 
9572.639388900254 	 Customer 9646 arrives for service at server 1 
9572.691850324678 	 Customer 9643 departs server 1
9572.691850324678 	 Customer 9

9657.30441880649 	 Customer 9723 departs server 1
9657.30441880649 	 Customer 9723 arrives for service at server 2
9657.922189050292 	 Customer 9722 departs server 2
9657.922189050292 	 Customer 9723 is being served at server 2
9658.453035620387 	 Customer 9723 departs server 2
9660.540938420058 	 Customer 9724 arrives for service at server 1 
9660.540938420058 	 Customer 9724 is being served at server 1
9660.759193971342 	 Customer 9725 arrives for service at server 1 
9661.145420353141 	 Customer 9724 departs server 1
9661.145420353141 	 Customer 9724 arrives for service at server 2
9661.145420353141 	 Customer 9724 is being served at server 2
9661.145420353141 	 Customer 9725 is being served at server 1
9661.20076665665 	 Customer 9724 departs server 2
9661.371607173134 	 Customer 9725 departs server 1
9661.371607173134 	 Customer 9725 arrives for service at server 2
9661.371607173134 	 Customer 9725 is being served at server 2
9661.611909461331 	 Customer 9725 departs server 2
9662

9752.514300524712 	 Customer 9806 arrives for service at server 2
9752.514300524712 	 Customer 9807 is being served at server 1
9752.524923464443 	 Customer 9807 departs server 1
9752.524923464443 	 Customer 9807 arrives for service at server 2
9752.524923464443 	 Customer 9808 is being served at server 1
9752.719643155935 	 Customer 9804 departs server 2
9752.719643155935 	 Customer 9805 is being served at server 2
9752.778859037251 	 Customer 9808 departs server 1
9752.778859037251 	 Customer 9808 arrives for service at server 2
9752.778859037251 	 Customer 9809 is being served at server 1
9752.821920115572 	 Customer 9805 departs server 2
9752.821920115572 	 Customer 9806 is being served at server 2
9752.962206799983 	 Customer 9810 arrives for service at server 1 
9753.277778355225 	 Customer 9809 departs server 1
9753.277778355225 	 Customer 9809 arrives for service at server 2
9753.277778355225 	 Customer 9810 is being served at server 1
9753.295567070052 	 Customer 9811 arrives 

9838.310884799028 	 Customer 9892 departs server 1
9838.310884799028 	 Customer 9892 arrives for service at server 2
9838.310884799028 	 Customer 9893 is being served at server 1
9839.01063516379 	 Customer 9893 departs server 1
9839.01063516379 	 Customer 9893 arrives for service at server 2
9839.01063516379 	 Customer 9894 is being served at server 1
9839.337713409268 	 Customer 9894 departs server 1
9839.337713409268 	 Customer 9894 arrives for service at server 2
9839.89825880737 	 Customer 9895 arrives for service at server 1 
9839.89825880737 	 Customer 9895 is being served at server 1
9840.728630221685 	 Customer 9895 departs server 1
9840.728630221685 	 Customer 9895 arrives for service at server 2
9840.89381947956 	 Customer 9896 arrives for service at server 1 
9840.89381947956 	 Customer 9896 is being served at server 1
9841.141887723365 	 Customer 9896 departs server 1
9841.141887723365 	 Customer 9896 arrives for service at server 2
9842.160148025754 	 Customer 9897 arrive

9937.693988535868 	 Customer 9974 departs server 1
9937.693988535868 	 Customer 9974 arrives for service at server 2
9938.445806022237 	 Customer 9970 departs server 2
9938.445806022237 	 Customer 9971 is being served at server 2
9939.306366382238 	 Customer 9975 arrives for service at server 1 
9939.306366382238 	 Customer 9975 is being served at server 1
9939.576849689136 	 Customer 9975 departs server 1
9939.576849689136 	 Customer 9975 arrives for service at server 2
9939.95689986247 	 Customer 9971 departs server 2
9939.95689986247 	 Customer 9972 is being served at server 2
9940.357081790018 	 Customer 9976 arrives for service at server 1 
9940.357081790018 	 Customer 9976 is being served at server 1
9940.75370813103 	 Customer 9977 arrives for service at server 1 
9941.014498499771 	 Customer 9972 departs server 2
9941.014498499771 	 Customer 9973 is being served at server 2
9941.514069252169 	 Customer 9976 departs server 1
9941.514069252169 	 Customer 9976 arrives for service 